In [24]:
from pydub import AudioSegment 
from pydub.utils import make_chunks
import os

def process_audio(file_name):
    
    myaudio = AudioSegment.from_file(file_name, "wav")
    myaudio = myaudio.set_channels(1)
    chunk_length_ms = 60000 # pydub calculates in millisec 
    chunks = make_chunks(myaudio,chunk_length_ms) #Make chunks of one minute 
    
    fname = file_name.split("\\")[-1].split(".")[0]
    
    for i, chunk in enumerate(chunks): 
        str_i = str(i)
        str_i = str_i.rjust(5, '0')
        chunk_name = f"..\\data\\08_project_mgmt_fsdl_splits\\{fname}_{str_i}.wav" 
        print ("exporting", chunk_name) 
        chunk.export(chunk_name, format="wav") 

In [25]:
# all_file_names = os.listdir()

# # try:
# #     os.makedirs("..\\data\\08_project_mgmt_fsdl_splits") # creating a folder named chunked
# # except:
# #     pass

# # for each_file in all_file_names:
# #     if ('.wav' in each_file):
# #         process_audio(each_file)

process_audio("..\\data\\08_project_mgmt_fsdl.wav")

exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00000.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00001.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00002.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00003.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00004.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00005.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00006.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00007.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00008.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00009.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00010.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00011.wav
exporting ..\data\08_project_mgmt_fsdl_splits\08_project_mgmt_fsdl_00012.wav

In [3]:
from txtai.pipeline import Transcription

# Create transcription model
transcribe = Transcription("openai/whisper-base")

C:\Users\Cooper\Documents\GitHub\txtai_pipelines\.venv\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [35]:
all_file_names = os.listdir("..\\data\\08_project_mgmt_fsdl_splits")
all_file_names = sorted(all_file_names)
# all_file_names

In [38]:
from txtai.embeddings import Embeddings, Documents
from txtai.workflow import FileTask, WorkflowTask
from txtai.workflow import Workflow, Task

data = os.listdir("..\\data\\08_project_mgmt_fsdl_splits")
data = sorted(data)
full_paths = [f"..\\data\\08_project_mgmt_fsdl_splits\\{x}" for x in data]
# data = ["..\\data\\08_project_mgmt_fsdl_splits\\08_project_mgmt_fsdl_0.wav"]
# data = ["..\\data\\test_audio_1.wav"]

tasks = [
    FileTask(transcribe, r"\.wav$")
]

workflow = Workflow(tasks)

with open(f"..\\data\\08_project_mgmt_fsdl_transcript_no_line_numbers.txt", "w") as f:
    for i, txt in enumerate(workflow(full_paths)):
        f.write(f"{txt}\n")


In [52]:
from txtai.pipeline import Summary

# Create summary model
summary = Summary("facebook/bart-large-cnn")


Downloading: 100%|████████████████████████████████████████████████████████████████| 1.58k/1.58k [00:00<00:00, 1.58MB/s]
Downloading: 100%|████████████████████████████████████████████████████████████████| 1.63G/1.63G [00:38<00:00, 42.7MB/s]
Downloading: 100%|███████████████████████████████████████████████████████████████████| 899k/899k [00:01<00:00, 704kB/s]
Downloading: 100%|██████████████████████████████████████████████████████████████████| 456k/456k [00:00<00:00, 2.46MB/s]
Downloading: 100%|████████████████████████████████████████████████████████████████| 1.36M/1.36M [00:00<00:00, 4.54MB/s]


In [48]:
with open("..\\data\\08_project_mgmt_fsdl_transcript_no_line_numbers.txt", "r") as f:
    document_text = f.readlines()
    
joined_doc = " ".join(document_text)

In [49]:
joined_doc = joined_doc.strip()

In [50]:
joined_doc

"Hey, everybody, welcome back. This week we're going to talk about something a little bit different than we do most weeks. Most weeks we talk about specific technical aspects of building machine learning powered products, but this week we're going to focus on some of the organizational things that you need to do in order to work together on ML powered products as part of an interdisciplinary team. So the reality of building ML powered products is that building any product well is really difficult. You have to figure out how to hire great people. You need to be able to manage\n of the organization against those requirements. But machine learning adds even more additional complexity to this. Machine learning talent tends to be very scarce and expensive to attract. Machine learning teams are not just a single role, but today they tend to be pretty interdisciplinary, which makes managing them an even bigger challenge. Machine learning projects often have unclear timelines, and there's a hi

In [53]:
summary(joined_doc)

"This week we're going to focus on some of the organizational things that you need to do in order to work together on ML powered products as part of an interdisciplinary team. Machine learning talent tends to be very scarce and expensive to attract. The work product is a trained model and oftentimes it's a report or a code repo."

In [57]:
stripped = [x.strip() for x in document_text]

In [84]:
# 5 minute summaries
new_data = []
i = 0
while i < len(stripped):
    if i < len(stripped)-5:
        new_data.append(" ".join(stripped[i:i+5]))
        i+=5
    else:
        new_data.append(" ".join(stripped[i:]))
        break
        
print(f"{len(new_data)=}")

summaries = []
for i, x in enumerate(new_data):
    print(f"summarizing {i} of {len(new_data)}")
    summaries.append(summary(x))

df = pd.DataFrame({"5m_sentences": new_data, "summaries_5m_sentences": summaries})

df.to_csv("5m_summaries.csv")

with open("5minute_summary_concat.txt", "w") as f:
    f.write("\n".join(summaries))

len(new_data)=13
summarizing 0 of 13
summarizing 1 of 13
summarizing 2 of 13
summarizing 3 of 13
summarizing 4 of 13
summarizing 5 of 13
summarizing 6 of 13
summarizing 7 of 13
summarizing 8 of 13
summarizing 9 of 13
summarizing 10 of 13
summarizing 11 of 13
summarizing 12 of 13


In [71]:
# merge every 3 items
new_data = []
i = 0
while i < len(stripped):
    if i < len(stripped)-2:
        new_data.append(" ".join(stripped[i:i+2]))
        i+=2
    else:
        new_data.append(" ".join(stripped[i:]))
        break

In [72]:
len(new_data)

33

In [70]:
len(stripped)

65

In [ ]:
summary(joined_doc)

In [73]:
summaries = []
for x in new_data:
    summaries.append(summary(x))

In [74]:
summaries

["This week we focus on some of the organizational things that you need to do in order to work together on ML powered products as part of an interdisciplinary team. Machine learning talent tends to be very scarce and expensive to attract. Machinelearning projects often have unclear timelines, and there's a high degree of uncertainty to those timelines.",
 "The goal is to help the rest of the stakeholders in your organization understand what they can really expect from the technology that you're building and what is realistic for us to achieve. We're going to talk about some of the unique aspects involved in hiring. or ML platform or ML info teams, machine learning engineers, machinelearning researchers, or ML scientists, data scientists.",
 "ML engineer is kind of a catch all is the ML researcher. This is a role that exists in some organizations that the responsibility stops after the model has been trained. These folks are focused on building models that are not yet production critica

In [78]:
len(stripped)

65

In [ ]:
summaries

In [79]:
import pandas as pd
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

df = pd.DataFrame({"triple_sentences": new_data, "summaries_triple_sentences": summaries})

In [81]:
df.to_csv("3m_summaries.csv")

In [82]:
with open("3minute_summary_concat.txt", "w") as f:
    f.write("\n".join(summaries))

In [15]:
from IPython.display import Audio, display

data = ["..\\data\\08_project_mgmt_fsdl_splits\\08_project_mgmt_fsdl_0.wav"]
# files = ["..\\data\\test_audio_1.wav"]

print(data)

for x, text in enumerate(transcribe(data)):
    display(Audio(data[x]))
    print(text)
    print()

['..\\data\\08_project_mgmt_fsdl_splits\\08_project_mgmt_fsdl_0.wav']


C:\Users\Cooper\Documents\GitHub\txtai_pipelines\.venv\lib\site-packages\transformers\generation_utils.py:1296: UserWarning: Neither `max_length` nor `max_new_tokens` has been set, `max_length` will default to 448 (`self.config.max_length`). Controlling `max_length` via the config is deprecated and `max_length` will be removed from the config in v5 of Transformers -- we recommend using `max_new_tokens` to control the maximum length of the generation.
  warnings.warn(


Hey, everybody, welcome back. This week we're going to talk about something a little bit different than we do most weeks. Most weeks we talk about specific technical aspects of building machine learning powered products, but this week we're going to focus on some of the organizational things that you need to do in order to work together on ML powered products as part of an interdisciplinary team. So the reality of building ML powered products is that building any product well is really difficult. You have to figure out how to hire great people. You need to be able to manage

